<a href="https://colab.research.google.com/github/annieedmonds/Homework/blob/main/DataProject1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [64]:
#imports
import requests
import json
import pandas as pd
import sqlite3 as sql

In [65]:
def read_file(file_name):
    if file_name.endswith('.csv'):
        try:
            df = pd.read_csv(file_name)
            print(f"Successfully read CSV file: {file_name}")
            return df
        except Exception as e:
            print(f"Error reading CSV file: {e}")
            return None
    elif file_name.startswith('https') and file_name.endswith('.json'):
        try:
            response = requests.get(file_name)
            if response.status_code == 200:
                print("Request successful")
                df = pd.json_normalize(response.json())
                return df
            else:
                raise Exception(f"Request failed with status code: {response.status_code}")
        except Exception as e:
            print(f"Error fetching data from URL: {e}")
            return None
    elif file_name.endswith('.json'):
        try:
            with open(file_name) as json_file:
                data = json.load(json_file)
                df = pd.json_normalize(data)
                print(f"Successfully read JSON file: {file_name}")
                return df
        except Exception as e:
            print(f"Error reading JSON file: {e}")
            return None
    else:
        print("Invalid file format")
        return None


In [66]:
#Retrieving a json
url = 'https://data.cityofnewyork.us/api/views/25th-nujf/rows.json?accessType=DOWNLOAD'
response = requests.get(url)
data = response.json()

#check the status code
if response.status_code == 200:
  print("Request successful")
else:
  print("Request failed")
data
json_df = pd.DataFrame(data['data'], columns=[c['name'] for c in data['meta']['view']['columns']])
json_df
#summary of the ingestion - number of records, number of columns
print(f"Ingested JSON data - Records: {len(json_df)}, Columns: {len(json_df.columns)}")

Request successful
Ingested JSON data - Records: 69214, Columns: 14


In [67]:
#Converting the json to csv
df = pd.DataFrame(data['data'], columns=[c['name'] for c in data['meta']['view']['columns']])
df.to_csv('data.csv', index=False)
df

sid                                    id  position  \
0      row-v4f5~xz3v-vr86  00000000-0000-0000-E0ED-52E8592E0A7A         0   
1      row-gdep~mr7x-dj3u  00000000-0000-0000-68AD-7B741D1DF31B         0   
2      row-4f22~xggt-ah4b  00000000-0000-0000-B276-36740F71A706         0   
3      row-rtrn~adrh.v7rc  00000000-0000-0000-14A3-C1AEC06ED345         0   
4      row-ncyh_z5tn~vyt2  00000000-0000-0000-F810-ECBD97111577         0   
...                   ...                                   ...       ...   
69209  row-nq2q.45uj.pd74  00000000-0000-0000-B802-EDAA90332AB8         0   
69210  row-5tzx.2ruv_ugsb  00000000-0000-0000-78B3-A1A6100D291D         0   
69211  row-k4h3-qgha_26eg  00000000-0000-0000-0C02-E3A41438D2D9         0   
69212  row-rp5w~izmw~qd99  00000000-0000-0000-CFB6-3634C6A5995D         0   
69213  row-keyt_r22s-zqun  00000000-0000-0000-53EA-98872707310C         0   

       created_at created_meta  updated_at updated_meta meta Year of Birth  \
0      1425766822         None  1425766822         None  { }          2011   
1      1425766822         None  1425766822         None  { }          2011   
2      1425766822         None  1425766822         None  { }          2011   
3      1425766822         None  1425766822         None  { }          2011   
4      1425766822         None  1425766822         None  { }          2011   
...           ...          ...         ...          ...  ...           ...   
69209  1717874305         None  1717874305         None  { }          2012   
69210  1717874305         None  1717874305         None  { }          2013   
69211  1717874305         None  1717874305         None  { }          2013   
69212  1717874305         None  1717874305         None  { }          2013   
69213  1717874305         None  1717874305         None  { }          2012   

       Gender           Ethnicity Child's First Name Count Rank  
0      FEMALE            HISPANIC          GERALDINE    13   75  
1      FEMALE            HISPANIC                GIA    21   67  
2      FEMALE            HISPANIC             GIANNA    49   42  
3      FEMALE            HISPANIC            GISELLE    38   51  
4      FEMALE            HISPANIC              GRACE    36   53  
...       ...                 ...                ...   ...  ...  
69209    MALE      BLACK NON HISP             CAYDEN    19   52  
69210  FEMALE  WHITE NON HISPANIC           Margaret    25   67  
69211  FEMALE  WHITE NON HISPANIC              Tamar    10   82  
69212  FEMALE  WHITE NON HISPANIC             Amanda    13   79  
69213  FEMALE            HISPANIC               ANNA    10   79  

[69214 rows x 14 columns]

In [46]:
#modify the number of columns
df.drop('id', inplace=True, axis=1)
df.drop('sid', inplace = True, axis=1)
df.drop('position', inplace = True, axis =1)
df.drop('updated_meta', inplace = True, axis =1)
df.drop('meta', inplace = True, axis =1)
df.drop('created_at', inplace = True, axis =1)
df.drop('created_meta', inplace = True, axis =1)
df.drop('updated_at', inplace = True, axis =1)
df

Year of Birth  Gender           Ethnicity Child's First Name Count Rank
0              2011  FEMALE            HISPANIC          GERALDINE    13   75
1              2011  FEMALE            HISPANIC                GIA    21   67
2              2011  FEMALE            HISPANIC             GIANNA    49   42
3              2011  FEMALE            HISPANIC            GISELLE    38   51
4              2011  FEMALE            HISPANIC              GRACE    36   53
...             ...     ...                 ...                ...   ...  ...
69209          2012    MALE      BLACK NON HISP             CAYDEN    19   52
69210          2013  FEMALE  WHITE NON HISPANIC           Margaret    25   67
69211          2013  FEMALE  WHITE NON HISPANIC              Tamar    10   82
69212          2013  FEMALE  WHITE NON HISPANIC             Amanda    13   79
69213          2012  FEMALE            HISPANIC               ANNA    10   79

[69214 rows x 6 columns]

In [47]:
#summary of post-processing:
print(f"Post-processed JSON data - Records: {len(df)}, Columns: {len(df.columns)}")

Post-processed JSON data - Records: 69214, Columns: 6


In [68]:
#Fetch/download/retrieve a csv file
df_csv = pd.read_csv('Air_Quality.csv')
df_csv

Unique ID  Indicator ID                                   Name  \
0         179772           640  Boiler Emissions- Total SO2 Emissions   
1         179785           640  Boiler Emissions- Total SO2 Emissions   
2         178540           365                Fine particles (PM 2.5)   
3         178561           365                Fine particles (PM 2.5)   
4         823217           365                Fine particles (PM 2.5)   
...          ...           ...                                    ...   
18020     816914           643          Annual vehicle miles traveled   
18021     816913           643          Annual vehicle miles traveled   
18022     816872           643          Annual vehicle miles traveled   
18023     816832           643          Annual vehicle miles traveled   
18024     151658           643          Annual vehicle miles traveled   

              Measure     Measure Info Geo Type Name  Geo Join ID  \
0      Number per km2           number         UHF42        409.0   
1      Number per km2           number         UHF42        209.0   
2                Mean           mcg/m3         UHF42        209.0   
3                Mean           mcg/m3         UHF42        409.0   
4                Mean           mcg/m3         UHF42        409.0   
...               ...              ...           ...          ...   
18020   Million miles  per square mile            CD        503.0   
18021   Million miles  per square mile            CD        503.0   
18022   Million miles  per square mile         UHF42        208.0   
18023   Million miles  per square mile         UHF42        407.0   
18024   Million miles  per square mile         UHF42        408.0   

                          Geo Place Name          Time Period  Start_Date  \
0                       Southeast Queens                 2015  01/01/2015   
1                Bensonhurst - Bay Ridge                 2015  01/01/2015   
2                Bensonhurst - Bay Ridge  Annual Average 2012  12/01/2011   
3                       Southeast Queens  Annual Average 2012  12/01/2011   
4                       Southeast Queens          Summer 2022  06/01/2022   
...                                  ...                  ...         ...   
18020  Tottenville and Great Kills (CD3)                 2019  01/01/2019   
18021  Tottenville and Great Kills (CD3)                 2010  01/01/2010   
18022               Canarsie - Flatlands                 2010  01/01/2010   
18023                   Southwest Queens                 2010  01/01/2010   
18024                            Jamaica                 2005  01/01/2005   

       Data Value  Message  
0             0.3      NaN  
1             1.2      NaN  
2             8.6      NaN  
3             8.0      NaN  
4             6.1      NaN  
...           ...      ...  
18020        12.9      NaN  
18021        14.7      NaN  
18022        43.4      NaN  
18023        65.8      NaN  
18024        41.0      NaN  

[18025 rows x 12 columns]

In [49]:
#summary of ingestion
print(f"Ingested CSV data - Records: {len(df_csv)}, Columns: {len(df_csv.columns)}")

Ingested CSV data - Records: 18025, Columns: 12


In [50]:
#modify the columns
df_csv.drop('Message', inplace = True, axis =1)
df_csv

Unique ID  Indicator ID                                   Name  \
0         179772           640  Boiler Emissions- Total SO2 Emissions   
1         179785           640  Boiler Emissions- Total SO2 Emissions   
2         178540           365                Fine particles (PM 2.5)   
3         178561           365                Fine particles (PM 2.5)   
4         823217           365                Fine particles (PM 2.5)   
...          ...           ...                                    ...   
18020     816914           643          Annual vehicle miles traveled   
18021     816913           643          Annual vehicle miles traveled   
18022     816872           643          Annual vehicle miles traveled   
18023     816832           643          Annual vehicle miles traveled   
18024     151658           643          Annual vehicle miles traveled   

              Measure     Measure Info Geo Type Name  Geo Join ID  \
0      Number per km2           number         UHF42        409.0   
1      Number per km2           number         UHF42        209.0   
2                Mean           mcg/m3         UHF42        209.0   
3                Mean           mcg/m3         UHF42        409.0   
4                Mean           mcg/m3         UHF42        409.0   
...               ...              ...           ...          ...   
18020   Million miles  per square mile            CD        503.0   
18021   Million miles  per square mile            CD        503.0   
18022   Million miles  per square mile         UHF42        208.0   
18023   Million miles  per square mile         UHF42        407.0   
18024   Million miles  per square mile         UHF42        408.0   

                          Geo Place Name          Time Period  Start_Date  \
0                       Southeast Queens                 2015  01/01/2015   
1                Bensonhurst - Bay Ridge                 2015  01/01/2015   
2                Bensonhurst - Bay Ridge  Annual Average 2012  12/01/2011   
3                       Southeast Queens  Annual Average 2012  12/01/2011   
4                       Southeast Queens          Summer 2022  06/01/2022   
...                                  ...                  ...         ...   
18020  Tottenville and Great Kills (CD3)                 2019  01/01/2019   
18021  Tottenville and Great Kills (CD3)                 2010  01/01/2010   
18022               Canarsie - Flatlands                 2010  01/01/2010   
18023                   Southwest Queens                 2010  01/01/2010   
18024                            Jamaica                 2005  01/01/2005   

       Data Value  
0             0.3  
1             1.2  
2             8.6  
3             8.0  
4             6.1  
...           ...  
18020        12.9  
18021        14.7  
18022        43.4  
18023        65.8  
18024        41.0  

[18025 rows x 11 columns]

In [51]:
#summary of post-processing:
print(f"Post-processed CSV data - Records: {len(df_csv)}, Columns: {len(df_csv.columns)}")

Post-processed CSV data - Records: 18025, Columns: 11


In [26]:
#Convert the general format and data structure of the data source
#Convert to json
json_data = df.to_json(orient = 'records')
json_data

'[{"Unique ID":179772,"Indicator ID":640,"Name":"Boiler Emissions- Total SO2 Emissions","Measure":"Number per km2","Measure Info":"number","Geo Type Name":"UHF42","Geo Join ID":409.0,"Geo Place Name":"Southeast Queens","Time Period":"2015","Start_Date":"01\\/01\\/2015","Data Value":0.3},{"Unique ID":179785,"Indicator ID":640,"Name":"Boiler Emissions- Total SO2 Emissions","Measure":"Number per km2","Measure Info":"number","Geo Type Name":"UHF42","Geo Join ID":209.0,"Geo Place Name":"Bensonhurst - Bay Ridge","Time Period":"2015","Start_Date":"01\\/01\\/2015","Data Value":1.2},{"Unique ID":178540,"Indicator ID":365,"Name":"Fine particles (PM 2.5)","Measure":"Mean","Measure Info":"mcg\\/m3","Geo Type Name":"UHF42","Geo Join ID":209.0,"Geo Place Name":"Bensonhurst - Bay Ridge","Time Period":"Annual Average 2012","Start_Date":"12\\/01\\/2011","Data Value":8.6},{"Unique ID":178561,"Indicator ID":365,"Name":"Fine particles (PM 2.5)","Measure":"Mean","Measure Info":"mcg\\/m3","Geo Type Name":"U

In [52]:
#choose your desired data source
df_datasource = input("Which data source would you like to use? (csv_df, json_df):").strip().lower()

Which data source would you like to use? (csv_df, json_df):csv_df


In [53]:
#import with chosen data source
if df_datasource == 'csv_df':
  df = df_csv
elif df_datasource == 'json_df':
  df = json_df
else:
  print("Invalid data source")

In [62]:
#Choose desired ouput
output_choice = input("Which output format would you like to use? (csv, json, sql):").strip().lower()

Which output format would you like to use? (csv, json, sql):sql


In [63]:
import sqlite3
#Export with chosen output
if output_choice == 'csv':
  df.to_csv('data.csv', index = False)
elif output_choice == 'json':
  df.to_json('data.json', orient = 'records')
elif output_choice == 'sql':
  conn = sqlite3.connect('data.db')
  df.to_sql('data', conn, if_exists = 'replace', index = False)
  conn.close()
  print("Data exported to SQL database")

  conn = sqlite3.connect('data.db')
  query = "SELECT * FROM data"
  df = pd.read_sql_query(query, conn)
  conn.close()
  print(df)
else:
  print("Invalid output format")



Data exported to SQL database
       Unique ID  Indicator ID                                   Name  \
0         179772           640  Boiler Emissions- Total SO2 Emissions   
1         179785           640  Boiler Emissions- Total SO2 Emissions   
2         178540           365                Fine particles (PM 2.5)   
3         178561           365                Fine particles (PM 2.5)   
4         823217           365                Fine particles (PM 2.5)   
...          ...           ...                                    ...   
18020     816914           643          Annual vehicle miles traveled   
18021     816913           643          Annual vehicle miles traveled   
18022     816872           643          Annual vehicle miles traveled   
18023     816832           643          Annual vehicle miles traveled   
18024     151658           643          Annual vehicle miles traveled   

              Measure     Measure Info Geo Type Name  Geo Join ID  \
0      Number per km2   

Reflection:

Some aspects of this project that I found more manageable than anticipated were the data format conversion and column modification. Converting the format from CSV to JSON was fairly easy and only consisted of a couple of lines of code. The only trouble I ran into at this stage was remembering to put the data in a data frame before converting from JSON to CSV. Furthermore, when producing a summary of the ingestion, I also needed to put the data into a data frame in JSON format. I also found the column modification of this project to be straightforward. My only modifications were dropping columns to make the data look cleaner and more easily readable. Therefore, I simply used the drop function and named the columns I wanted to delete. I based the deleted columns on columns that either had missing values or were empty.

The aspects of this project that I found more difficult were deciding on the order of the code, handling two separate data sources, and error handling. At first, I had trouble deciding where to put in the input() functions for the user to choose their desired data source and output. I was initially going to have it at the beginning of my code, but then I discovered it made more sense to have it at the end. Furthermore, deciding where to put the column modification code was tricky. I eventually found that it was easiest to have the modification after the conversion when it was from JSON to CSV and before the conversion when it was from CSV to JSON. I did this because deciding how to modify the data in the CSV format was easier. I ran into various errors throughout the project, and handling each error as I worked through the project became tedious.

A utility like this would be helpful for other projects because it is an easy way to convert data to a different format quickly. Some projects require different formats, whether SQL, CSV, or JSON. Therefore, this utility allows users to choose the format they want to work with and allows for easy adaptability. Furthermore, if projects require data from multiple sources, an ETL can help handle various data sources simultaneously. Another benefit of an ETL is that it is useful when handling large datasets and adapting to different scalability.